In [1]:
from dbfread import DBF
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import geopandas as gpd
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split
import datetime



import os
import ee
from google.auth.transport.requests import Request
from google.oauth2.credentials import Credentials
from google_auth_oauthlib.flow import InstalledAppFlow
import csv
import datetime
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor, as_completed

import logging
import json

# Configuration du logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

from time import sleep


Index(['profile_id', 'profile_code', 'dataset_code', 'site_id',
       'positional_uncertainty', 'country_name', 'longitude', 'latitude',
       'wrb_reference_soil_group_code', 'wrb_reference_soil_group',
       'wrb_prefix_qualifiers', 'wrb_suffix_qualifiers',
       'wrb_principal_qualifiers', 'wrb_supplementary_qualifiers',
       'wrb_publication_year', 'fao_major_group_code', 'fao_major_group',
       'fao_soil_unit_code', 'fao_soil_unit', 'fao_publication_year',
       'usda_order_name', 'usda_suborder', 'usda_subgroup', 'usda_great_group',
       'usda_publication_year'],
      dtype='object')


profile_id   longitude   latitude  wrb_publication_year  \
400        1144527    3.883333   7.483333                2014.0   
402        1144529  152.850000 -26.183333                1998.0   
404        1144531 -122.561111  49.263889                1998.0   
405        1144532  -18.247778  65.774167                2006.0   
410        1144537   -5.416667  15.383333                2006.0   
...            ...         ...        ...                   ...   
215301     1667090   28.516667 -14.300000                2006.0   
215307     1667096  -20.916667  64.166667                2006.0   
223274     1686942   37.050000  -6.950000                2014.0   
223275     1686943   37.050000  -6.816667                2014.0   
223359     1687027   30.683333 -29.766667                2007.0   

        fao_publication_year  usda_publication_year  
400                   1974.0                 1975.0  
402                   1997.0                 1975.0  
404                   1997.0                 1975.0  
405                   1997.0                 1999.0  
410                   1997.0                 1975.0  
...                      ...                    ...  
215301                1997.0                 1987.0  
215307                1997.0                 1988.0  
223274                1997.0                 2014.0  
223275                1997.0                 2014.0  
223359                1997.0                 1999.0  

[2808 rows x 6 columns]

In [18]:
# Lire les couches


profiles = pd.DataFrame(iter(DBF('../data/use/afsp/GIS_Dbf/AfSP012Qry_Profiles.dbf', encoding='latin-1')))

profiles

# X_LonDD	Y_LatDD	T_Year
# Lire les profils géoréférencés
geo = gpd.read_file('../data/use/afsp/GIS_Shape/AfSP012Qry_GeoPoints.shp')
geo['Longitude'] = geo.geometry.x
geo['Latitude'] = geo.geometry.y



# Fusionner les deux sur 'ProfileID'
merged = pd.merge(profiles, geo[['ProfileID', 'Longitude', 'Latitude']], on='ProfileID', how='left')
# X_LonDD	Y_LatDD	XYAccur	T_Year



# print(merged[['ProfileID', 'LayerID', 'Sand', 'Clay', 'PHH2O', 'OrgC', 'Longitude', 'Latitude']].head())
# suppression les  profiles sans coordonnées
profiles_ = merged.dropna(subset=['Longitude', 'Latitude'])

# Afficher les profils géoréférencés
profiles_ = profiles_[['ProfileID', 'Longitude', 'Latitude','T_Year']]
# profiles_['T_Year'] = pd.to_datetime(profiles_['T_Year'], errors='coerce').dt.year

profiles_

#convert the T_Year to int
profiles_['T_Year'] = pd.to_numeric(profiles_['T_Year'], errors='coerce').astype('Int64')

# afficher toute les date avec le poucentage de chaque année
year_counts = profiles_['T_Year'].value_counts(normalize=True) * 100
# print("\nPourcentage de profils par année :")
print(year_counts)

# Afficher les années avec le pourcentage
year_counts = year_counts.reset_index()
profiles_

#afficher les années  unique
unique_years = profiles_['T_Year'].unique()
print("\nAnnées uniques dans les profils géoréférencés :", unique_years)


T_Year
-9999    11.881509
1988      8.449792
1989      6.987536
1997      4.289645
1990      4.030648
           ...    
1945      0.053958
1953      0.016187
1942      0.010792
1938      0.005396
1941      0.005396
Name: proportion, Length: 68, dtype: Float64

Années uniques dans les profils géoréférencés : <IntegerArray>
[ 1957,  1963,  1962,  1966,  1960,  1954,  1958,  1965,  1964,  1956,  1952,
  1961,  1969,  1955,  1959,  1968,  1970,  1951,  1967,  1986,  1997,  1980,
  1981,  1984,  1982,  1983,  1987, -9999,  1996,  1995,  1994,  1998,  1999,
  1988,  1990,  1991,  1977,  1989,  1985,  1979,  1992,  1978,  1974,  1976,
  1973,  1975,  1971,  2000,  2004,  1993,  2003,  2002,  1972,  2001,  2006,
  2007,  2008,  1941,  1938,  1945,  2009,  2005,  1942,  1944,  2010,  1946,
  1953,  2011]
Length: 68, dtype: Int64


In [19]:
# Portée requise par Earth Engine
# SCOPES = ["https://www.googleapis.com/auth/earthengine.readonly"]



# def authenticate_earth_engine():
    
#     creds = None

#     # Vérifie si token.json existe (authentification précédente)
#     if os.path.exists("token.json"):
#         creds = Credentials.from_authorized_user_file("token.json", SCOPES)

#     # Sinon, lance le flow OAuth pour obtenir un token
#     if not creds or not creds.valid:
#         if creds and creds.expired and creds.refresh_token:
#             creds.refresh(Request())
#         else:
#             flow = InstalledAppFlow.from_client_secrets_file(
#                 "credentials.json", SCOPES
                
#             )
#             creds = flow.run_local_server(port=0)

#         # Sauvegarde le token pour les prochaines fois
#         with open("token.json", "w") as token:
#             token.write(creds.to_json())

#     # Initialisation Earth Engine avec les credentials OAuth
#     ee.Initialize(credentials=creds)
#     print(" Earth Engine authentifié avec succès !")

# # Authentification Earth Engine
# authenticate_earth_engine()


# Initialisation Earth Engine
SCOPES = ["https://www.googleapis.com/auth/earthengine.readonly"]

def initialize_earth_engine():
    """Initialise Earth Engine avec les credentials"""
    try:
        creds = Credentials.from_authorized_user_file("token.json", SCOPES)
        ee.Initialize(credentials=creds)
        logger.info("Earth Engine initialisé avec succès")
    except Exception as e:
        logger.error(f"Erreur d'initialisation Earth Engine: {str(e)}")
        raise

In [45]:


initialize_earth_engine()

def get_sentinel_data(point, start_date, end_date):
    """
    Récupère les données Sentinel-2 pour un point donné et une période.
    
    Args:
        point (ee.Geometry.Point): Point géographique.
        start_date (str): Date de début au format 'YYYY-MM-DD'.
        end_date (str): Date de fin au format 'YYYY-MM-DD'.
        
    Returns:
        ee.ImageCollection: Collection d'images Sentinel-2 filtrée.
    """
    start_date , end_date ,sat = "2015-06-01", "2016-01-01", "COPERNICUS/S2"
    collection = ee.ImageCollection("COPERNICUS/S2") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 20)
    )
    # Prendre l'image la moins nuageuse
    if not collection.size().getInfo():
        # logger.warning(f"Aucune image trouvée pour la période {start_date} à {end_date} pour le point {point.getInfo()}")
        return start_date, end_date, sat, None
    
    image = collection.first()
    
    # Vérifier les bandes disponibles
    available_bands = image.bandNames().getInfo()
    if not available_bands:
        # logger.warning(f"Aucune bande valide trouvée")
        return start_date, end_date, sat, None
    
    # Récupérer les informations des bandes
    bands_info = {}
    for band in available_bands:
        info = get_band_info(image, band)
        if info:
            bands_info[band] = info[band]  # Utiliser le nom de la bande comme clé
            # # bands_name : value. min_value, max_value, etc.
            # bands_info.append({
            #     f"B_{band[1:]}": {
            #         "value": info.get("value"),
            #         "min_value": info.get("min_value"),
            #         "max_value": info.get("max_value")
            #     }
            # })

    if not bands_info:
        # logger.warning("Aucune information de bande récupérée")
        return start_date, end_date, sat, None
    
    return start_date, end_date, sat, bands_info
        
        
# Dictionnaire des satellites Landsat
# LANDSAT_COLLECTIONS = {
#     "Landsat-1": {"years": (1972, 1978), "path": "LANDSAT/LM01/C02/T2", "bands": ["B4", "B5", "B6", "B7", "QA_PIXEL"]},
#     "Landsat-2": {"years": (1975, 1981), "path": "LANDSAT/LM02/C02/T1", "bands": ["B4", "B5", "B6", "B7", "QA_PIXEL"]},
#     "Landsat-3": {"years": (1978, 1983), "path": "LANDSAT/LM03/C02/T1", "bands": ["B4", "B5", "B6", "B7", "QA_PIXEL"]},
#     "Landsat-4": {"years": (1982, 1993), "path": "LANDSAT/LM04/C02/T1", "bands": ["B1", "B2", "B3", "B4", "B5", "B7", "QA_PIXEL"]},
#     "Landsat-5": {"years": (1984, 2013), "path": "LANDSAT/LM05/C02/T1", "bands": ["B1", "B2", "B3", "B4", "B5", "B7", "QA_PIXEL"]}
# }
LANDSAT_COLLECTIONS = {
    "Landsat-1": {
        "years": (1972, 1978),
        "path": "LANDSAT/LM01/C02/T2",
        "bands": ["B4", "B5", "B6", "B7", "QA_PIXEL"]
    },
    "Landsat-2": {
        "years": (1975, 1981),
        "path": "LANDSAT/LM02/C02/T1",
        "bands": ["B4", "B5", "B6", "B7", "QA_PIXEL"]
    },
    "Landsat-3": {
        "years": (1978, 1983),
        "path": "LANDSAT/LM03/C02/T1",
        "bands": ["B4", "B5", "B6", "B7", "QA_PIXEL"]
    },
    "Landsat-4": {
        "years": (1982, 1993),
        "path": "LANDSAT/LT04/C02/T1_L2",
        "bands": ["SR_B1", "SR_B2", "SR_B3", "SR_B4", "SR_B5", "SR_B7", "QA_PIXEL"]
    },
    "Landsat-5": {
        "years": (1984, 2013),
        "path": "LANDSAT/LT05/C02/T1_L2",
        "bands": ["SR_B1", "SR_B2", "SR_B3", "SR_B4", "SR_B5", "SR_B7", "QA_PIXEL"]
    },
    "Landsat-7": {
        "years": (1999, 2022),
        "path": "LANDSAT/LE07/C02/T1_L2",
        "bands": ["SR_B1", "SR_B2", "SR_B3", "SR_B4", "SR_B5", "SR_B7", "QA_PIXEL"]
    },
    "Landsat-8": {
        "years": (2013, 2025),  # en fonction de la dernière date disponible
        "path": "LANDSAT/LC08/C02/T1_L2",
        "bands": ["SR_B1", "SR_B2", "SR_B3", "SR_B4", "SR_B5", "SR_B6", "SR_B7", "SR_B10", "SR_B11", "QA_PIXEL"]
    },
    "Landsat-9": {
        "years": (2021, 2025),  # pareil, à adapter
        "path": "LANDSAT/LC09/C02/T1_L2",
        "bands": ["SR_B1", "SR_B2", "SR_B3", "SR_B4", "SR_B5", "SR_B6", "SR_B7", "SR_B10", "SR_B11", "QA_PIXEL"]
    }
}

def get_appropriate_satellite(year):
    """Trouve le satellite Landsat approprié pour une année donnée"""
    year = int(year)
    
    if year < 1972:
        logger.info(f"Année {year} avant le début de Landsat, utilisation de 1972 comme proxy")
        year = 1972
    
    for name, info in LANDSAT_COLLECTIONS.items():
        start, end = info["years"]
        if start <= year <= end:
            return name, info["path"], info["bands"], year

    logger.debug(f"Année {year} après la fin de Landsat-5, utilisation de 2013 comme proxy")
    return "Landsat-5", LANDSAT_COLLECTIONS["Landsat-5"]["path"], LANDSAT_COLLECTIONS["Landsat-5"]["bands"], 2013

# def get_band_info(image, band_name):
#     """Récupère les informations détaillées d'une bande"""
#     try:
#         band = image.select(band_name)
#         return {
#             'crs': band.projection().getInfo()['crs'],
#             'transform': band.projection().getInfo()['transform'],
#             'data_type': band.getInfo()['bands'][0]['data_type'],
#             'dimensions': band.getInfo()['bands'][0]['dimensions']
#         }
#     except Exception as e:
#         logger.warning(f"Erreur lors de la récupération des infos pour la bande {band_name}: {str(e)}")
#         return None

def get_band_info(image, band_name):
    """Récupère les informations détaillées d'une bande"""
    try:
        band = image.select(band_name)
        stats = band.reduceRegion(
            # reducer=ee.Reducer.minMax(),
            reducer=ee.Reducer.mean(),
            geometry=image.geometry(),
            scale=60,
            # bestEffort=True
        ).getInfo()
        
        # print(f"Stats pour la bande {band_name}: {stats}")
        return {
            # 'crs': band.projection().getInfo()['crs'],
            # 'transform': band.projection().getInfo()['transform'],
            # 'data_type': band.getInfo()['bands'][0]['data_type'],
            # 'dimensions': band.getInfo()['bands'][0]['dimensions'],
            band_name: stats.get(f'{band_name}'),
        }
    except Exception as e:
        logger.warning(f"Erreur lors de la récupération des infos pour la bande {band_name}: {str(e)}")
        return None

def get_landsat_data(point, target_year):
    """
    Récupère les données Landsat pour un point et une année cible
    """
    try:
        # Vérifier les coordonnées valides
        coords = point.coordinates().getInfo()
        if coords == [0, 0] or None in coords:
            logger.warning("Coordonnées invalides - point ignoré")
            error = "get_landsat_data 1 : Coordonnées invalides - point ignoré"
            return None, None, None, None ,error

        # Trouver le satellite approprié
        sat_name, sat_path, target_bands, effective_year = get_appropriate_satellite(target_year)
        
        # Période de recherche (±3 ans autour de l'année cible)
     
        start_date = f"{target_year}-01-01"
        end_date = f"{target_year}-12-31"
        
        logger.debug(f"Recherche {sat_name} ({start_date} à {end_date}) pour {coords}")

        # Créer la collection d'images
        collection = ee.ImageCollection(sat_path) \
            .filterDate(start_date, end_date) \
            .filterBounds(point) \
            .sort('CLOUD_COVER', True)
        
        # Vérifier si des images sont disponibles
        count = collection.size().getInfo()
        if count == 0:
            logger.debug(f"Aucune image trouvée pour {sat_name} {start_date}-{end_date}")
            error = f"get_landsat_data 1 : Aucune image trouvée pour {sat_name} {start_date}-{end_date}"
            return start_date, end_date, sat_name, None ,error

        # Prendre l'image la moins nuageuse
        images = collection.all()
        for image in images:
        # Vérifier les bandes disponibles
            available_bands = image.bandNames().getInfo()
            valid_bands = [b for b in target_bands if b in available_bands]
            
            if not valid_bands:
                logger.debug(f"Aucune bande valide trouvée parmi {target_bands}")
                error = f"get_landsat_data 1 : Aucune bande valide trouvée parmi {target_bands}"
                # return start_date, end_date, sat_name, None ,error
                return start_date, end_date, sat_name, None ,error

            # Récupérer les informations des bandes
            bands_info = {}
            for band in valid_bands:
                info = get_band_info(image, band)
                if info:
                    bands_info[band] = info[band]  # Utiliser le nom de la bande comme clé
                    # # bands_name : value. min_value, max_value, etc.
                    # bands_info.append({
                    #     f"B_{band[1:]}": {
                    #         "value": info.get("value"),
                    #         "min_value": info.get("min_value"),
                    #         "max_value": info.get("max_value")
                    #     }
                # })

        if not bands_info:
            logger.debug("Aucune information de bande récupérée")
            error ="get_landsat_data 1 : Aucune information de bande récupérée"
            return start_date, end_date, sat_name, None ,error
        
        return start_date, end_date, sat_name, bands_info,None
        
    except Exception as e:
        logger.debug(f"Erreur lors du traitement du point {coords}: {str(e)}")
        error = f"get_landsat_data 1 : Erreur lors du traitement du point {coords}: {str(e)}"
        return None, None, None, None ,error

def process_row(row):
    """Traite une ligne du dataframe"""
    try:
        profile_id, lon, lat, year = row
        
        # Créer le point géographique
        point = ee.Geometry.Point(lon, lat)
        
        # Récupérer les données Landsat
        start_date, end_date, sat_name, bands_info ,error = get_landsat_data(point, int(year))
        # start_date, end_date, sat_name, bands_info = get_sentinel_data(point, start_date="2015-06-01", end_date="2025-01-01")

        if bands_info is None:
            logger.info(f"Aucune donnée pour {profile_id}")
            bands_data = {"error": error}
        else:
            bands_data = bands_info

        return {
            'ProfileID': profile_id,
            'Longitude': lon,
            'Latitude': lat,
            'T_Year': year,
            'Start_Date': start_date,
            'End_Date': end_date,
            'Satellite': sat_name,
            
            

        } ,bands_data

    except Exception as e:
        logger.error(f"Erreur pour le profil {row[0]}: {str(e)}")
        return None

def main( output_csv,profiles_=profiles_):
    """Fonction principale"""
    # Charger les données d'entrée
    # df = pd.read_csv(input_csv)
    # profiles_list = df[['ProfileID', 'Longitude', 'Latitude', 'T_Year']].values.tolist()
    
    # Check if the output file already exists et le creer si nécessaire
    if not os.path.exists(output_csv):
        with open(output_csv, 'w', newline='') as f:
            writer = csv.writer(f)
            writer.writerow(['ProfileID', 'Longitude', 'Latitude', 'T_Year', 'Start_Date', 'End_Date', 'Satellite'])
            
    
    print("before filtering:", profiles_.shape)
    profiles_ = profiles_[profiles_['T_Year'] >= 1972 ]
    profiles_ = profiles_[ profiles_['T_Year'] <= 2013]
    print("after filtering year:", profiles_.shape)
    available_years = profiles_['T_Year'].unique()

    # print("available years:", pd.Series(available_years).sort_values())
    
    # filter longitude and latitude
    profiles_ = profiles_[(profiles_['Longitude'] != 0.0) &
                          (profiles_['Latitude'] != 0.0) &
                          (profiles_['Longitude'].notnull()) &
                          (profiles_['Latitude'].notnull())]
    print("after filtering coordinates:", profiles_.shape)  
    # suppression des profils sans coordonnées
    # profiles_ = profiles_.dropna(subset=['Longitude', 'Latitude'])
    # prendre le premier profil pour les coordonnées indentiques
    profiles_ = profiles_.drop_duplicates(subset=['Longitude', 'Latitude'], keep='first')
    print("after removing duplicates:", profiles_.shape)
    
    # print("after filtering coordinates:", profiles_.shape)"""  """





    profiles_list =  profiles_[['ProfileID', 'Longitude', 'Latitude','T_Year']].values.tolist()
    # eliminer les profils sans coordonnées
    # profiles_list = [p for p in profiles_list if p[1] != 0.0 and p[2] != 0.0]
    # eliminer les profils avec des coordonnées nulles


    already_get_data = pd.read_csv(output_csv)

    # Filtrer les profils déjà traités
    processed_profiles = already_get_data['ProfileID'].tolist()
    profiles_list = [p for p in profiles_list if p[0] not in processed_profiles]
    print(f"Nombre de profils à traiter : {len(profiles_list)}")
    # prendre les 5000 premiers profils pour le test
    profiles_list = profiles_list[:1000]


    results = []
    
    # Traitement parallèle
    with ThreadPoolExecutor(max_workers=6) as executor:
        futures = [executor.submit(process_row, row) for row in profiles_list]
        
        for future in tqdm(as_completed(futures), total=len(futures), desc="Traitement des profils"):
            result , bands_data = future.result()
            if result:
                results.append({**result, **bands_data})

    # Sauvegarder les résultats
    output_df = pd.DataFrame(results)
    # data_to_save = already_get_data.append(output_df, ignore_ind"""  """ex=True)
    data_to_save = pd.concat([already_get_data, output_df], ignore_index=True)

    data_to_save.to_csv(output_csv, index=False)
    logger.info(f"Résultats sauvegardés dans {output_csv}")
    

if __name__ == "__main__":
    # Configuration des fichiers


    OUTPUT_CSV = "lansat_new_results_improved.csv"

    main(OUTPUT_CSV)

INFO:__main__:Earth Engine initialisé avec succès


before filtering: (18533, 4)
after filtering year: (13406, 4)
after filtering coordinates: (12940, 4)
after removing duplicates: (11676, 4)
Nombre de profils à traiter : 9665


Traitement des profils:   0%|          | 2/1000 [00:00<05:21,  3.10it/s]INFO:__main__:Aucune donnée pour MW lrep_BL71
INFO:__main__:Aucune donnée pour MW lrep_BL76
Traitement des profils:   0%|          | 5/1000 [00:01<04:02,  4.11it/s]INFO:__main__:Aucune donnée pour MW lrep_BL77
INFO:__main__:Aucune donnée pour MW lrep_BL80
INFO:__main__:Aucune donnée pour MW lrep_BL8
Traitement des profils:   1%|          | 10/1000 [00:02<04:19,  3.81it/s]INFO:__main__:Aucune donnée pour MW lrep_BL82
INFO:__main__:Aucune donnée pour MW lrep_BL73
INFO:__main__:Aucune donnée pour MW lrep_BL75
INFO:__main__:Aucune donnée pour MW lrep_BL74
INFO:__main__:Aucune donnée pour MW lrep_BL83
Traitement des profils:   2%|▏         | 16/1000 [00:03<02:34,  6.35it/s]INFO:__main__:Aucune donnée pour MW lrep_BL85
INFO:__main__:Aucune donnée pour MW lrep_BL89
INFO:__main__:Aucune donnée pour MW lrep_BL87
INFO:__main__:Aucune donnée pour MW lrep_BL9
Traitement des profils:   2%|▏         | 20/1000 [00:03<01:55,  8.51

In [44]:



collection = ee.ImageCollection("LANDSAT/LC08/C02/T1_L2")
print(collection.first().getInfo())


{'type': 'Image', 'bands': [{'id': 'SR_B1', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [9161, 9161], 'crs': 'EPSG:32628', 'crs_transform': [30, 0, 341085, 0, -30, 8808015]}, {'id': 'SR_B2', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [9161, 9161], 'crs': 'EPSG:32628', 'crs_transform': [30, 0, 341085, 0, -30, 8808015]}, {'id': 'SR_B3', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [9161, 9161], 'crs': 'EPSG:32628', 'crs_transform': [30, 0, 341085, 0, -30, 8808015]}, {'id': 'SR_B4', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [9161, 9161], 'crs': 'EPSG:32628', 'crs_transform': [30, 0, 341085, 0, -30, 8808015]}, {'id': 'SR_B5', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [9161, 9161], 'crs': 'EPSG:32628', 'crs_transform': [30, 0, 341085, 0, -30

In [4]:
initialize_earth_engine()

def get_sentinel_annual_medians(point, start_year=2015, end_year=2025):
    """
    Pour un point donné, calcule la médiane annuelle des bandes Sentinel-2 de 2015 à 2025.
    """
    results = []

    for year in range(start_year, end_year + 1):
        start_date = f"{year}-01-01"
        end_date = f"{year}-12-31"

        collection = (
            ee.ImageCollection("COPERNICUS/S2_SR_HARMONIZED")
            .filterBounds(point)
            .filterDate(start_date, end_date)
            .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 20))
        )

        if collection.size().getInfo() == 0:
            continue  # Aucune image cette année-là

        # Calculer l’image médiane de l’année
        median_image = collection.median()

        # Extraire la moyenne des valeurs au point
        bands = median_image.bandNames().getInfo()
        band_values = {}

        for band in bands:
            try:
                value = median_image.select(band).reduceRegion(
                    reducer=ee.Reducer.mean(),
                    geometry=point,
                    scale=10,
                    bestEffort=True
                ).getInfo().get(band)
                band_values[band] = value
            except Exception as e:
                band_values[band] = None

        results.append({
            'Year': year,
            **band_values
        })

    return results


def process_row(row):
    try:
        profile_id, lon, lat, t_year = row
        if lon == 0.0 or lat == 0.0:
            return []
        point = ee.Geometry.Point(lon, lat)

        annual_medians = get_sentinel_annual_medians(point)

        results = []
        for record in annual_medians:
            result = {
                'ProfileID': profile_id,
                'Longitude': lon,
                'Latitude': lat,
                'T_Year': t_year,
                'Data_Year': record['Year'],
                **{k: v for k, v in record.items() if k != 'Year'}
            }
            results.append(result)

        return results
    except Exception as e:
        logger.error(f"Erreur pour le profil {row[0]}: {str(e)}")
        return []






def main(output_csv):
    # profiles_list = df[['ProfileID', 'Longitude', 'Latitude', 'T_Year']].values.tolist()
    
    profiles_list =  profiles_[['ProfileID', 'Longitude', 'Latitude','T_Year']].values.tolist()
    
    # checker si le fichier de résultats existe déjà
    if not os.path.exists(output_csv):
        # Si le fichier n'existe pas, on crée une liste vide pour les résultats
        already_get_data = pd.DataFrame(columns=[
            'ProfileID', 'Longitude', 'Latitude', 'T_Year', 'Image_Date'
        ])

    else:
        already_get_data = pd.read_csv(output_csv)

    # Filtrer les profils déjà traités
    processed_profiles = already_get_data['ProfileID'].tolist()
    profiles_list = [p for p in profiles_list if p[0] not in processed_profiles]
    print(f"Nombre de profils à traiter : {len(profiles_list)}")
    # prendre les 5000 premiers profils pour le test
    profiles_list = profiles_list[:5000]
    results = []

    with ThreadPoolExecutor(max_workers=8) as executor:
        futures = [executor.submit(process_row, row) for row in profiles_list]

        for future in tqdm(as_completed(futures), total=len(futures), desc="Traitement des profils"):
            all_results = future.result()
            
            results.extend(all_results)
      

    output_df = pd.DataFrame(results)
    data_to_save = pd.concat([already_get_data, output_df], ignore_index=True)
    data_to_save.to_csv(output_csv, index=False)
    
main("sentinel_results_improved_all.csv")

INFO:__main__:Earth Engine initialisé avec succès


Nombre de profils à traiter : 16823


Traitement des profils: 100%|██████████| 5000/5000 [39:50:00<00:00, 28.68s/it]  


In [ ]:


initialize_earth_engine()

def get_sentinel_data(point, start_date, end_date):
    """
    Récupère les données Sentinel-2 pour un point donné et une période.
    
    Args:
        point (ee.Geometry.Point): Point géographique.
        start_date (str): Date de début au format 'YYYY-MM-DD'.
        end_date (str): Date de fin au format 'YYYY-MM-DD'.
        
    Returns:
        ee.ImageCollection: Collection d'images Sentinel-2 filtrée.
    """
    start_date , end_date ,sat = "2015-06-01", "2016-01-01", "COPERNICUS/S2"
    collection = ee.ImageCollection("COPERNICUS/S2") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 20)
    )
    # Prendre l'image la moins nuageuse
    if not collection.size().getInfo():
        # logger.warning(f"Aucune image trouvée pour la période {start_date} à {end_date} pour le point {point.getInfo()}")
        return start_date, end_date, sat, None
    
    image = collection.first()
    
    # Vérifier les bandes disponibles
    available_bands = image.bandNames().getInfo()
    if not available_bands:
        # logger.warning(f"Aucune bande valide trouvée")
        return start_date, end_date, sat, None
    
    # Récupérer les informations des bandes
    bands_info = {}
    for band in available_bands:
        info = get_band_info(image, band)
        if info:
            bands_info[band] = info[band]  # Utiliser le nom de la bande comme clé
            # # bands_name : value. min_value, max_value, etc.
            # bands_info.append({
            #     f"B_{band[1:]}": {
            #         "value": info.get("value"),
            #         "min_value": info.get("min_value"),
            #         "max_value": info.get("max_value")
            #     }
            # })

    if not bands_info:
        # logger.warning("Aucune information de bande récupérée")
        return start_date, end_date, sat, None
    
    return start_date, end_date, sat, bands_info
        
        
def get_band_info(image, band_name):
    """Récupère les informations détaillées d'une bande"""
    try:
        band = image.select(band_name)
        stats = band.reduceRegion(
            # reducer=ee.Reducer.minMax(),
            reducer=ee.Reducer.mean(),
            geometry=image.geometry(),
            scale=60,
            # bestEffort=True
        ).getInfo()
        
        # print(f"Stats pour la bande {band_name}: {stats}")
        return {
            # 'crs': band.projection().getInfo()['crs'],
            # 'transform': band.projection().getInfo()['transform'],
            # 'data_type': band.getInfo()['bands'][0]['data_type'],
            # 'dimensions': band.getInfo()['bands'][0]['dimensions'],
            band_name: stats.get(f'{band_name}'),
        }
    except Exception as e:
        logger.warning(f"Erreur lors de la récupération des infos pour la bande {band_name}: {str(e)}")
        return None


def process_row(row):
    """Traite une ligne du dataframe"""
    try:
        profile_id, lon, lat, year = row
        
        # Créer le point géographique
        point = ee.Geometry.Point(lon, lat)
        
        # Récupérer les données Landsat
        # start_date, end_date, sat_name, bands_info = get_landsat_data(point, int(year))
        start_date, end_date, sat_name, bands_info = get_sentinel_data(point, start_date="2015-06-01", end_date="2025-01-01")

        if bands_info is None:
            logger.info(f"Aucune donnée pour {profile_id}")
            bands_data = {}
        else:
            bands_data = bands_info

        return {
            'ProfileID': profile_id,
            'Longitude': lon,
            'Latitude': lat,
            'T_Year': year,
            'Start_Date': start_date,
            'End_Date': end_date,
            'Satellite': sat_name,
            
            

        } ,bands_data

    except Exception as e:
        logger.error(f"Erreur pour le profil {row[0]}: {str(e)}")
        return None

def main( output_csv):
    """Fonction principale"""
    # Charger les données d'entrée
    # df = pd.read_csv(input_csv)
    # profiles_list = df[['ProfileID', 'Longitude', 'Latitude', 'T_Year']].values.tolist()
    
    profiles_list =  profiles_[['ProfileID', 'Longitude', 'Latitude','T_Year']].values.tolist()
    
    already_get_data = pd.read_csv('sentinel_results_improved.csv')

    # Filtrer les profils déjà traités
    processed_profiles = already_get_data['ProfileID'].tolist()
    profiles_list = [p for p in profiles_list if p[0] not in processed_profiles]
    print(f"Nombre de profils à traiter : {len(profiles_list)}")
    # prendre les 5000 premiers profils pour le test
    # profiles_list = profiles_list[:5000]


    results = []
    
    # Traitement parallèle
    with ThreadPoolExecutor(max_workers=6) as executor:
        futures = [executor.submit(process_row, row) for row in profiles_list]
        
        for future in tqdm(as_completed(futures), total=len(futures), desc="Traitement des profils"):
            result , bands_data = future.result()
            if result:
                results.append({**result, **bands_data})

    # Sauvegarder les résultats
    output_df = pd.DataFrame(results)
    # data_to_save = already_get_data.append(output_df, ignore_ind"""  """ex=True)
    data_to_save = pd.concat([already_get_data, output_df], ignore_index=True)

    data_to_save.to_csv(output_csv, index=False)
    logger.info(f"Résultats sauvegardés dans {output_csv}")
    

if __name__ == "__main__":
    # Configuration des fichiers

    OUTPUT_CSV = "sentinel_results_all_improved.csv"

    main(OUTPUT_CSV)

In [5]:

output_df.to_csv("sentinel_results_improved.csv", index=False)

NameError: name 'output_df' is not defined

In [ ]:
from concurrent.futures import ThreadPoolExecutor, as_completed
SCOPES = ["https://www.googleapis.com/auth/earthengine.readonly"]

def init_worker_earth_engine():
    creds = Credentials.from_authorized_user_file("token.json", SCOPES)
    ee.Initialize(credentials=creds)
def get_sentinel_data(point, start_date, end_date):
    """
    Récupère les données Sentinel-2 pour un point donné et une période.
    
    Args:
        point (ee.Geometry.Point): Point géographique.
        start_date (str): Date de début au format 'YYYY-MM-DD'.
        end_date (str): Date de fin au format 'YYYY-MM-DD'.
        
    Returns:
        ee.ImageCollection: Collection d'images Sentinel-2 filtrée.
    """
    start_date , end_date ,sat = "2015-06-01", "2016-01-01", "COPERNICUS/S2"
    return start_date, end_date, sat, ee.ImageCollection("COPERNICUS/S2") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 20))

def get_landsat_data(point,T_year):
    """
    Récupère les données Landsat pour un point donné et une période.
    
    Args:
        point (ee.Geometry.Point): Point géographique.
        start_date (str): Date de début au format 'YYYY-MM-DD'.
        end_date (str): Date de fin au format 'YYYY-MM-DD'.
        

        Landsat-1 : 1972-1978
        Landsat-2 : 1975-1981
        Landsat-3 : 1978-1983	Landsat-4 : 1982-1993
        Landsat-5 : 1984-2013
        

        Bande 1 - Aérosols	0,433 - 0,453 µm	30 m
        Bande 2 - Bleu	0,450 - 0,515 µm	30 m
        Bande 3 - Vert	0,525 - 0,600 µm	30 m
        Bande 4 - Rouge	0,630 - 0,680 µm	30 m
        Bande 5 - Infrarouge proche	0,845 - 0,885 µm	30 m
        Bande 6 - Infrarouge moyen 1	1,560 - 1,660 µm	30 m
        Bande 7 - Infrarouge moyen 2	2,100 - 2,300 µm	30 m
        Bande 8 - Panchromatique	0,500 - 0,680 µm	15 m
        Bande 9 - Cirrus	1,360 - 1,390 µm	30 m
    Returns:
        ee.ImageCollection: Collection d'images Landsat filtrée.
        ddd
    """

    landsat = {"Landsat-1": [(1972,1978), "LANDSAT/LM01/C02/T2"],
               "Landsat-2": [(1975,1981), "LANDSAT/LM02/C02/T1"],
               "Landsat-3": [(1978,1983), "LANDSAT/LM03/C02/T1"],
               "Landsat-4": [(1982,1993), "LANDSAT/LM04/C02/T1"],
               "Landsat-5": [(1984,2013), "LANDSAT/LM05/C02/T1"]}
  

    if T_year < 1972 or T_year > 2013:
        T_year = 1972
        # raise ValueError(f"L'année {T_year} doit être comprise entre 1972 et 2013 pour Landsat.")



    if T_year in range(1972, 1979):
        start_date = f"{landsat['Landsat-1'][0][0]}-01-01"
        end_date = f"{landsat['Landsat-1'][0][1]}-12-31"
        sat = landsat["Landsat-1"][1]
    elif T_year in range(1979, 1982):
        start_date = f"{landsat['Landsat-2'][0][0]}-01-01"
        end_date = f"{landsat['Landsat-2'][0][1]}-12-31"
        sat = landsat["Landsat-2"][1]
    elif T_year in range(1982, 1984):
        start_date = f"{landsat['Landsat-3'][0][0]}-01-01"
        end_date = f"{landsat['Landsat-3'][0][1]}-12-31"
        sat = landsat["Landsat-3"][1]
    elif T_year in range(1984, 1994):
        start_date = f"{landsat['Landsat-4'][0][0]}-01-01"
        end_date = f"{landsat['Landsat-4'][0][1]}-12-31"
        sat = landsat["Landsat-4"][1]
    elif T_year in range(1994, 2014):
        start_date = f"{landsat['Landsat-5'][0][0]}-01-01"
        end_date = f"{landsat['Landsat-5'][0][1]}-12-31"
        sat = landsat["Landsat-5"][1]
    else:
        raise ValueError("L'année doit être comprise entre 1972 et 2013 pour Landsat.")

  


    # start_date = '1974-01-01'
    # end_date = '1974-12-31'
    # point = ee.Geometry.Point(6.746, 46.529,)


    col = ee.ImageCollection(sat) \
            .filterDate(start_date, end_date) \
            .filterBounds(point)
        
    if col.size().getInfo() == 0:
        return start_date, end_date, sat, None
        # raise ValueError("Aucune image Landsat pour ce point et cette période.")"""  """

    image = col.median()
    available_bands = image.bandNames().getInfo()
    target_bands = ["B4", "B5", "B6", "B7", "QA_PIXEL", "QA_RADSAT"]
    valid_bands = [b for b in target_bands if b in available_bands]
    bands = image.select(available_bands)
    # print(bands.getInfo())



    if not valid_bands:
        raise ValueError(f"Aucune des bandes {target_bands} n'est présente dans cette image.")

    return start_date, end_date, sat, bands
        
    # .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 20))

collection_data = {}
landsat = {}

profiles__list = profiles_[['ProfileID', 'Longitude', 'Latitude','T_Year']].values.tolist()

total_size = 0
start_at = 0

def process_row(row):
    try:
        profile_id, lon, lat, year = row
        point = ee.Geometry.Point(lon, lat)
        start_date, end_date, sat, collection = get_sentinel_data(point, start_date="2015-06-01", end_date="2025-01-01")
        # start_date, end_date, sat, collection = get_landsat_data(point, int(year))
        if collection is None:
            bands = []
           
        
        else:
            values = collection.getInfo()
            bands = values.get('bands', [])
            print(f"Récupération des données pour {profile_id} : {start_date} à {end_date}, Satellite: {sat}, Bandes: {bands}")

        return {
            'ProfileID': profile_id,
            'Longitude': lon,
            'Latitude': lat,
            'T_Year': year,
            'Start_Date': start_date,
            'End_Date': end_date,
            'Bands': bands
        }
    except Exception as e:
        print(f"Erreur pour {row[0]}: {e}")
        return None

with ThreadPoolExecutor(max_workers=6) as executor:
    futures = [executor.submit(process_row, row) for row in profiles__list]
    results = []
    for f in tqdm(as_completed(futures), total=len(futures)):
        res = f.result()
        break
        if res:
            results.append(res)

landsat_df = pd.DataFrame(results)
landsat_df.to_csv("landsat_threaded.csv", index=False)


  0%|          | 0/18533 [00:01<?, ?it/s]

Récupération des données pour AO SOTER_P.107/66 : 1972-01-01 à 1978-12-31, Satellite: LANDSAT/LM01/C02/T2, Bandes: [{'id': 'B4', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B5', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B6', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B7', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'QA_PIXEL', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 65535}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'QA_RADSAT', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 65535}, 'crs': 'EPSG:

Récupération des données pour AO SOTER_P.1/57 : 1972-01-01 à 1978-12-31, Satellite: LANDSAT/LM01/C02/T2, Bandes: [{'id': 'B4', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B5', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B6', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B7', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'QA_PIXEL', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 65535}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'QA_RADSAT', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 65535}, 'crs': 'EPSG:43

KeyboardInterrupt: 

Récupération des données pour AO SOTER_P.147/59 : 1972-01-01 à 1978-12-31, Satellite: LANDSAT/LM01/C02/T2, Bandes: [{'id': 'B4', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B5', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B6', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'B7', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 255}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'QA_PIXEL', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 65535}, 'crs': 'EPSG:4326', 'crs_transform': [1, 0, 0, 0, 1, 0]}, {'id': 'QA_RADSAT', 'data_type': {'type': 'PixelType', 'precision': 'double', 'min': 0, 'max': 65535}, 'crs': 'EPSG:

In [ ]:
from concurrent.futures import ThreadPoolExecutor, as_completed
import ee
from google.oauth2.credentials import Credentials
import pandas as pd
from tqdm import tqdm

import logging

# Configuration du logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# Initialisation Earth Engine
SCOPES = ["https://www.googleapis.com/auth/earthengine.readonly"]

def initialize_earth_engine():
    """Initialise Earth Engine avec les credentials"""
    try:

        creds = Credentials.from_authorized_user_file("token.json", SCOPES)
        ee.Initialize(credentials=creds)
        logger.info("Earth Engine initialisé avec succès")
    except Exception as e:
        logger.error(f"Erreur d'initialisation Earth Engine: {str(e)}")
        raise

initialize_earth_engine()

# Dictionnaire des satellites Landsat
LANDSAT_COLLECTIONS = {
    "Landsat-1": {"years": (1972, 1978), "path": "LANDSAT/LM01/C02/T2"},
    "Landsat-2": {"years": (1975, 1981), "path": "LANDSAT/LM02/C02/T1"},
    "Landsat-3": {"years": (1978, 1983), "path": "LANDSAT/LM03/C02/T1"}, 
    "Landsat-4": {"years": (1982, 1993), "path": "LANDSAT/LM04/C02/T1"},
    "Landsat-5": {"years": (1984, 2013), "path": "LANDSAT/LM05/C02/T1"}
}
def get_sentinel_data(point, start_date, end_date):
    """
    Récupère les données Sentinel-2 pour un point donné et une période.
    
    Args:
        point (ee.Geometry.Point): Point géographique.
        start_date (str): Date de début au format 'YYYY-MM-DD'.
        end_date (str): Date de fin au format 'YYYY-MM-DD'.
        
    Returns:
        ee.ImageCollection: Collection d'images Sentinel-2 filtrée.
    """
    start_date , end_date ,sat = "2015-06-01", "2016-01-01", "COPERNICUS/S2"
    return start_date, end_date, sat, ee.ImageCollection("COPERNICUS/S2") \
        .filterBounds(point) \
        .filterDate(start_date, end_date) \
        .filter(ee.Filter.lt("CLOUDY_PIXEL_PERCENTAGE", 20))

def get_appropriate_satellite(year):
    """Trouve le satellite Landsat approprié pour une année donnée"""
    year = int(year)
    
    if year < 1972:
        logger.warning(f"Année {year} avant le début de Landsat, utilisation de 1972 comme proxy")
        year = 1972
    
    for name, info in LANDSAT_COLLECTIONS.items():
        start, end = info["years"]
        if start <= year <= end:
            return name, info["path"], year
    
    # Si année après 2013, utiliser Landsat-5 (dernier disponible)
    logger.warning(f"Année {year} après la fin de Landsat-5, utilisation de 2013 comme proxy")
    return "Landsat-5", LANDSAT_COLLECTIONS["Landsat-5"]["path"], 2013

def get_landsat_data(point, target_year):
    """
    Récupère les données Landsat pour un point et une année cible
    
    Args:
        point (ee.Geometry.Point): Point géographique
        target_year (int): Année cible
        
    Returns:
        tuple: (start_date, end_date, satellite, bands_info)
    """
    try:
        # Vérifier les coordonnées valides
        if point.coordinates().getInfo() == [0, 0]:
            logger.warning("Coordonnées (0,0) - point invalide")
            return None, None, None, None

        # Trouver le satellite approprié
        sat_name, sat_path, effective_year = get_appropriate_satellite(target_year)
        
        # Définir la période de recherche (±2 ans autour de l'année cible)
        start_year = max(effective_year - 2, 1972)
        end_year = min(effective_year + 2, 2013)
        
        start_date = f"{start_year}-01-01"
        end_date = f"{end_year}-12-31"
        
        logger.info(f"Recherche {sat_name} ({start_date} à {end_date}) pour {point.getInfo()}")

        # Créer la collection d'images
        collection = ee.ImageCollection(sat_path) \
            .filterDate(start_date, end_date) \
            .filterBounds(point) \
            .sort('CLOUD_COVER', True)  # Tri par couverture nuageuse
        
        # Vérifier si des images sont disponibles
        count = collection.size().getInfo()
        if count == 0:
            logger.warning(f"Aucune image trouvée pour {sat_name} {start_date}-{end_date}")
            return start_date, end_date, sat_name, None
        
        # Prendre l'image la moins nuageuse
        image = collection.first()
        
        # Extraire les bandes disponibles
        available_bands = image.bandNames().getInfo()
        target_bands = ["B1", "B2", "B3", "B4", "B5", "B6", "B7", "QA_PIXEL"]
        valid_bands = [b for b in target_bands if b in available_bands]
        
        if not valid_bands:
            logger.warning(f"Aucune bande valide trouvée parmi {target_bands}")
            return start_date, end_date, sat_name, None
        
        # Créer le dictionnaire des bandes
        bands_info = []
        for band in valid_bands:
            band_info = {
                'name': band,
                'description': image.get(band).getInfo(),
                'crs': image.select(band).projection().getInfo()
            }
            bands_info.append(band_info)
        
        return start_date, end_date, sat_name, bands_info
        
    except Exception as e:
        logger.error(f"Erreur lors du traitement du point {point.getInfo()}: {str(e)}")
        return None, None, None, None

def process_row(row):
    """Traite une ligne du dataframe"""
    try:
        profile_id, lon, lat, year = row
        
        # Créer le point géographique
        point = ee.Geometry.Point(lon, lat)
        
        # Récupérer les données Landsat
        start_date, end_date, sat_name, bands_info = get_landsat_data(point, int(year))
        
        if bands_info is None:
            logger.info(f"Aucune donnée pour {profile_id}")
            bands_data = []
        else:
            bands_data = [{"band": b['name'], "info": b['description']} for b in bands_info]
        
        return {
            'ProfileID': profile_id,
            'Longitude': lon,
            'Latitude': lat,
            'T_Year': year,
            'Start_Date': start_date,
            'End_Date': end_date,
            'Satellite': sat_name,
            'Bands': bands_data
        }
        
    except Exception as e:
        logger.error(f"Erreur pour le profil {row[0]}: {str(e)}")
        return None

def main(input_csv, output_csv):
    """Fonction principale"""
    # Charger les données d'entrée
    # df = pd.read_csv(input_csv)
    profiles_list =  profiles_[['ProfileID', 'Longitude', 'Latitude','T_Year']].values.tolist()
    
    results = []
    
    # Traitement parallèle
    with ThreadPoolExecutor(max_workers=6) as executor:
        futures = [executor.submit(process_row, row) for row in profiles_list]
        
        for future in tqdm(as_completed(futures), total=len(futures), desc="Traitement des profils"):
            result = future.result()
            if result:
                results.append(result)
    
    # Sauvegarder les résultats
    output_df = pd.DataFrame(results)
    output_df.to_csv(output_csv, index=False)
    logger.info(f"Résultats sauvegardés dans {output_csv}")

if __name__ == "__main__":
    # Configuration des fichiers
    INPUT_CSV = "profiles_input.csv"  # Remplacez par votre fichier d'entrée
    OUTPUT_CSV = "landsat_results.csv"
    
    main(INPUT_CSV, OUTPUT_CSV)

INFO:__main__:Earth Engine initialisé avec succès
Traitement des profils:   0%|          | 0/18533 [00:00<?, ?it/s]WARNING:__main__:Année 1957 avant le début de Landsat, utilisation de 1972 comme proxy
INFO:__main__:Recherche Landsat-1 (1972-01-01 à 1974-12-31) pour {'type': 'Point', 'coordinates': [17.573093, -10.950086]}
INFO:__main__:Recherche Landsat-1 (1972-01-01 à 1974-12-31) pour {'type': 'Point', 'coordinates': [15.107436, -10.07856]}
INFO:__main__:Recherche Landsat-1 (1972-01-01 à 1974-12-31) pour {'type': 'Point', 'coordinates': [14.10162, -15.955931]}
INFO:__main__:Recherche Landsat-1 (1972-01-01 à 1974-12-31) pour {'type': 'Point', 'coordinates': [17.573781, -14.194014]}
INFO:__main__:Recherche Landsat-1 (1972-01-01 à 1974-12-31) pour {'type': 'Point', 'coordinates': [12.161278, -15.222598]}
INFO:__main__:Recherche Landsat-1 (1972-01-01 à 1974-12-31) pour {'type': 'Point', 'coordinates': [14.635114, -6.152014]}
Traitement des profils:   0%|          | 5/18533 [00:05<3:01:43

In [ ]:
import pandas as pd

def create_csv(profile_id, longitude, latitude, year, start_date, end_date, satellite_name, band_values_dict):
    """
    Crée une ligne formatée pour le CSV final.
    
    Args:
        profile_id (str/int)
        longitude (float)
        latitude (float)
        year (int)
        start_date (str) : "YYYY-MM-DD"
        end_date (str) : "YYYY-MM-DD"
        satellite_name (str)
        band_values_dict (dict) : {'B1': val1, 'B2': val2, ..., 'Bn': valn}

    Returns:
        pandas.DataFrame : une seule ligne formatée
    """
    base_info = {
        "ProfileID": profile_id,
        "Longitude": longitude,
        "Latitude": latitude,
        "T_Year": year,
        "Start_Date": start_date,
        "End_Date": end_date,
        "Satellite": satellite_name
    }

    # Renommage pour avoir les colonnes B_1, B_2, etc.
    bands = {f"B_{band[1:]}" if band.startswith("B") else band: val for band, val in band_values_dict.items()}

    row_data = {**base_info, **bands}
    return pd.DataFrame([row_data])

# 🔧 Exemple d'utilisation
row_df = create_csv(
    profile_id=1,
    longitude=-16.5,
    latitude=14.7,
    year=2022,
    start_date="2022-06-01",
    end_date="2022-06-30",
    satellite_name="Sentinel-2",
    band_values_dict={
        "B1": 0.12,
        "B2": 0.15,
        "B3": 0.18,
        "B4": 0.20,
        "NDVI": 0.55
    }
)

# Ajouter à un CSV
csv_path = "result.csv"
row_df.to_csv(csv_path, index=False)
print(f"CSV généré : {csv_path}")


In [8]:
# Calcul des indices de végétation
def compute_indices(image):
    ndvi = image.normalizedDifference(['B8', 'B4']).rename('NDVI')
    gdvi = image.expression('(NIR - GREEN)', {
        'NIR': image.select('B8'),
        'GREEN': image.select('B3')
    }).rename('GDVI')
    msavi2 = image.expression(
        '0.5 * (2 * NIR + 1 - sqrt((2 * NIR + 1) ** 2 - 8 * (NIR - RED)))',
        {
            'NIR': image.select('B8'),
            'RED': image.select('B4')
        }
    ).rename('MSAVI2')
    psrinir = image.expression('(NIR / RED) ** 2', {
        'NIR': image.select('B8'),
        'RED': image.select('B4')
    }).rename('PSRINIR')
    ndwi = image.normalizedDifference(['B8', 'B11']).rename('NDWI')
    cigreen = image.expression('(NIR / GREEN) - 1', {
        'NIR': image.select('B8'),
        'GREEN': image.select('B3')
    }).rename('CIGreen')
    return image.addBands([ndvi, gdvi, msavi2, psrinir, ndwi, cigreen])

# Récupération des features pour un point
def get_features(profile_id, lat, lon, date_str, days_interval=5):
    try:
        point = ee.Geometry.Point([lon, lat])
        date = datetime.datetime.strptime(date_str, '%Y-%m-%d')
        start = (date - datetime.timedelta(days=days_interval)).strftime('%Y-%m-%d')
        end = (date + datetime.timedelta(days=days_interval)).strftime('%Y-%m-%d')

        s2 = ee.ImageCollection("COPERNICUS/S2_SR") \
            .filterBounds(point) \
            .filterDate(start, end) \
            .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 20))

        if s2.size().getInfo() == 0:
            raise ValueError("Pas d'image Sentinel-2 disponible")

        s2_img = compute_indices(s2.median())

        bands_s2 = ['B1','B2','B3','B4','B5','B6','B7','B8','B8A','B9','B10','B11','B12',
                    'NDVI','GDVI','MSAVI2','PSRINIR','NDWI','CIGreen']

        s2_result = s2_img.select(bands_s2).reduceRegion(
            reducer=ee.Reducer.mean(),
            geometry=point,
            scale=10,
            maxPixels=1e9
        ).getInfo()

        dem = ee.Image("USGS/SRTMGL1_003")
        mnt_value = dem.reduceRegion(
            reducer=ee.Reducer.mean(),
            geometry=point,
            scale=30
        ).get('elevation').getInfo()

        result = {
            'ProfileID': profile_id,
            'Latitude': lat,
            'Longitude': lon,
            'Date': date_str,
            'MNT_1': mnt_value
        }
        result.update(s2_result)
        return result, None

    except Exception as e:
        return None, {
            'ProfileID': profile_id,
            'Latitude': lat,
            'Longitude': lon,
            'Date': date_str,
            'Error': str(e)
        }

# Liste de points d'exemple (à remplacer par votre propre dataset)
points = [
    {'ProfileID': 1, 'Latitude': 12.161278, 'Longitude': -15.222598, 'Date': '2017-06-15'},
    {'ProfileID': 2, 'Latitude': 13.5, 'Longitude': -14.5, 'Date': '2019-08-20'}
]

# Fichiers de sortie
output_file = "sentinel_features.csv"
error_file = "sentinel_errors.csv"

# Extraction des données
features_list = []
errors_list = []

for pt in points:
    result, error = get_features(pt['ProfileID'], pt['Latitude'], pt['Longitude'], pt['Date'])
    if result:
        features_list.append(result)
    if error:
        errors_list.append(error)

# Sauvegarde des résultats
if features_list:
    with open(output_file, 'w', newline='') as f:
        writer = csv.DictWriter(f, fieldnames=features_list[0].keys())
        writer.writeheader()
        writer.writerows(features_list)

if errors_list:
    with open(error_file, 'w', newline='') as f:
        writer = csv.DictWriter(f, fieldnames=errors_list[0].keys())
        writer.writeheader()
        writer.writerows(errors_list)

output_file, error_file


/Users/magayendiaye/projects/soc/env/lib/python3.13/site-packages/ee/deprecation.py:207: DeprecationWarning: 

Attention required for COPERNICUS/S2_SR! You are using a deprecated asset.
To make sure your code keeps working, please update it.
Learn more: https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S2_SR

  warnings.warn(warning, category=DeprecationWarning)


('sentinel_features.csv', 'sentinel_errors.csv')

In [17]:
print(f"Nombre de profils avec données Sentinel-2 : {len(sentinel_2)+start_at}")


Nombre de profils avec données Sentinel-2 : 9079
